In [1]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

## Data Scraping

In [2]:
from bs4 import BeautifulSoup
import requests
from pathlib import Path

In [3]:

def scrap_data(wiki_link, save_file_path = "/Prabir/knowledge_graph/data_input/cureus/movie.txt"):
    wikipedia_movie_link = wiki_link
    
    page_to_scrape = requests.get(wikipedia_movie_link)
    soup = BeautifulSoup(page_to_scrape.text, "html.parser")
    
    para = ''
    for paragraph in soup.select('p'):
        p = paragraph.getText()
        para += p


     # Open the file in write mode and save the paragraph
    with open(save_file_path, 'w') as file:
        file.write(para)
    
    print(f"Paragraph saved to {save_file_path}")

## Loading Document

In [4]:
import pandas as pd
import numpy as np
import os
from langchain.document_loaders import PyPDFLoader, UnstructuredPDFLoader, PyPDFium2Loader
from langchain.document_loaders import PyPDFDirectoryLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from pathlib import Path
import random

from helpers.df_helpers import documents2Dataframe

In [5]:
## Input data directory
data_dir = "cureus"
inputdirectory = Path(f"./data_input/{data_dir}")
## This is where the output csv files will be written
out_dir = data_dir
outputdirectory = Path(f"./data_output/{out_dir}")

In [6]:
# def load_document(inputdirectory):
#     loader = DirectoryLoader(inputdirectory, show_progress=True)
#     documents = loader.load()
    
#     splitter = RecursiveCharacterTextSplitter(
#         chunk_size=1500,
#         chunk_overlap=150,
#         length_function=len,
#         is_separator_regex=False,
#     )
    
#     pages = splitter.split_documents(documents)
#     # print("Number of chunks = ", len(pages))
#     # print(pages[3].page_content)

#     # Create dataframe of chunks
#     df = documents2Dataframe(pages)
#     print("from load document")
#     print(df.head())
#     # df.head()
    
    # return df

## Node generation

In [14]:
# !pip install langchain
# !pip install -U langchain-community
# !pip install unstructured
# !sudo apt-get install libmagic1
# !pip install yachalk
#ollama serve
#ollama run zephyr

In [15]:
## This function uses the helpers/prompt function to extract concepts from text
from helpers.df_helpers import df2Graph
from helpers.df_helpers import graph2Df

In [16]:
# def node_generation(df):
#     ## To regenerate the graph with LLM, set this to True
#     regenerate = True
    
#     if regenerate:
#         concepts_list = df2Graph(df, model='zephyr:latest')
#         dfg1 = graph2Df(concepts_list)
#         if not os.path.exists(outputdirectory):
#             os.makedirs(outputdirectory)
        
#         dfg1.to_csv(outputdirectory/"graph.csv", sep="|", index=False)
#         df.to_csv(outputdirectory/"chunks.csv", sep="|", index=False)
#     else:
#         dfg1 = pd.read_csv(outputdirectory/"graph.csv", sep="|")
    
#     dfg1.replace("", np.nan, inplace=True)
#     dfg1.dropna(subset=["node_1", "node_2", 'edge'], inplace=True)
#     dfg1['count'] = 4 
#     ## Increasing the weight of the relation to 4. 
#     ## We will assign the weight of 1 when later the contextual proximity will be calculated. 

#     print("from node generation")
#     print(dfg1.shape)
#     print(dfg1.head())

#     return dfg1

## Strat from here

In [17]:
# !pip install openpyxl

In [18]:
import pandas as pd
import os

In [19]:
columns = ["YoR", "movie_name", "imdb_rating", "wiki_link", "popular"]
movie_links = pd.read_excel("Movie_list.xlsx", sheet_name = "hollywood")
movie_links.columns = columns
# movie_links.head()

In [20]:
popular_movie_links = movie_links[movie_links.popular == "popular"]
least_popular_movie_links = movie_links[movie_links.popular == "Least popular"]
# least_popular_movie_links.head()

In [21]:
root_output_folder = "/Prabir/knowledge_graph/hollywood/"
movie_categories = [least_popular_movie_links, popular_movie_links]

for movie_category in movie_categories:
    for index, row in movie_category.iterrows():
        try:
            movie_name = row["movie_name"]
            YoR = row["YoR"]
            wiki_link = row["wiki_link"]
            popular = row["popular"]

            # scrape data from the given link and store the data in the data_input directory
            scrap_data(wiki_link)

            #load document in dataframe chunk
            loader = DirectoryLoader(inputdirectory, show_progress=True)
            documents = loader.load()
            
            splitter = RecursiveCharacterTextSplitter(
                chunk_size=1500,
                chunk_overlap=150,
                length_function=len,
                is_separator_regex=False,
            )            
            pages = splitter.split_documents(documents)

            
            # Create dataframe of chunks
            df = documents2Dataframe(pages)

            #node generation task
            ## To regenerate the graph with LLM, set this to True
            regenerate = True
            
            if regenerate:
                concepts_list = df2Graph(df, model='zephyr:latest')
                dfg1 = graph2Df(concepts_list)
                if not os.path.exists(outputdirectory):
                    os.makedirs(outputdirectory)
                
                dfg1.to_csv(outputdirectory/"graph.csv", sep="|", index=False)
                df.to_csv(outputdirectory/"chunks.csv", sep="|", index=False)
            else:
                dfg1 = pd.read_csv(outputdirectory/"graph.csv", sep="|")
            
            dfg1.replace("", np.nan, inplace=True)
            dfg1.dropna(subset=["node_1", "node_2", 'edge'], inplace=True)
            dfg1['count'] = 4 



            
            
            #save the nodes dataframe in csv_file
            save_folder_name = popular
            save_file_name = movie_name + "_" + str(YoR) + ".csv"
            save_path = os.path.join(root_output_folder, save_folder_name, save_file_name)      
            dfg1.to_csv(save_path, index=False)

        except:
            continue

Paragraph saved to /Prabir/knowledge_graph/data_input/cureus/movie.txt


100%|██████████| 1/1 [00:02<00:00,  2.42s/it]




ERROR ### Here is the buggy response:  [
   {
       "node_1": "Pearl Harbor",
       "node_2": "Imperial Japanese Navy",
       "edge": "The Imperial Japanese Navy begins its attack on Pearl Harbor, severely damaging the US Pacific Fleet and most of the defending airfields before they can launch fighters to defend the harbor."
   },
   {
       "node_1": "Rafe",
       "node_2": "Danny",
       "edge": "On the night of December 6, Evelyn discovers Rafe standing outside her door and later they get into a fight at the Hula bar after Danny finds a drunken Rafe with the intention of reconciling."
   },
   {
       "node_1": "Pearl Harbor",
       "node_2": "US Pacific Fleet",
       "edge": "The Imperial Japanese Navy begins its attack on Pearl Harbor, severely damaging the US Pacific Fleet and most of the defending airfields before they can launch fighters to defend the harbor."
   },
   {
       "node_1": "Pearl Harbor",
       "node_2": "USS Oklahoma",
       "edge": "The survivors a

100%|██████████| 1/1 [00:00<00:00, 122.34it/s]


Paragraph saved to /Prabir/knowledge_graph/data_input/cureus/movie.txt


...



ERROR ### Here is the buggy response:  [
   {
      "node_1": "Guardians of the Galaxy",
      "node_2": "Marvel Cinematic Universe",
      "edge": "Guardians of the Galaxy is a part of the Marvel Cinematic Universe, which consists of various superhero films produced by Marvel Studios and distributed by Walt Disney Studios Motion Pictures."
   },
   {
      "node_1": "Guardians of the Galaxy Vol. 3",
      "node_2": "Guardians of the Galaxy",
      "edge": "Guardians of the Galaxy Vol. 3 is a sequel to Guardians of the Galaxy, which is also a part of the Marvel Cinematic Universe."
   },
   {
      "node_1": "Marvel Comics superhero team",
      "node_2": "Guardians of the Galaxy",
      "edge": "Guardians of the Galaxy is based on the Marvel Comics superhero team with the same name."
   },
   {
      "node_1": "Chris Pratt",
      "node_2": "Guardians of the Galaxy Vol. 3",
      "edge": "Chris Pratt, who played Starlord/Peter Quill in Guardians of the Galaxy and its sequel, will al

100%|██████████| 1/1 [00:00<00:00,  8.68it/s]




ERROR ### Here is the buggy response:  [
  {
    "node_1": "John Wick",
    "node_2": "Ballerina",
    "edge": "Lance Reddick's character Charon was the concierge of the Continental hotel, a hub for assassins in the John Wick universe. In Ballerina, which takes place between John Wick: Chapter 3 - Parabellum and John Wick: Chapter 4, it is revealed that Charon played a role in the events leading up to Ballerina's story. Thus, John Wick can be considered related to the spin-off movie Ballerina."
  },
  {
    "node_1": "John Wick",
    "node_2": "The Continental: From the World of John Wick",
    "edge": "Many characters from the John Wick movies, including Winston (Ian McShane) and John Wick (Keanu Reeves), frequented the Continental hotel in their respective movies. The spin-off TV series, which follows a younger version of these characters, can be considered related to John Wick due to the shared setting and character connections."
  },
  {
    "node_1": "Caine",
    "node_2": "John

100%|██████████| 1/1 [00:00<00:00,  4.45it/s]




ERROR ### Here is the buggy response:  [
   {
       "node_1": "Amy Schumer",
       "node_2": "Title role (in the original script)",
       "edge": "In December 2016, Amy Schumer entered negotiations for the title role with Winston's screenplay."
   },
   {
       "node_1": "Amy Schumer",
       "node_2": "Sister (Kim Caramele)",
       "edge": "She helped rewrite the script with her sister, Kim Caramele,"
   },
   {
       "node_1": "Title role",
       "node_2": "Amy Schumer",
       "edge": "In December 2016, Amy Schumer entered negotiations for the title role with Winston's screenplay.",
   },
   {
       "node_1": "Scheduling conflicts",
       "node_2": "Amy Schumer",
       "edge": "She revealed in 2023 that she left due to creative differences with the film's producers."
   },
   {
       "node_1": "Anne Hathaway",
       "node_2": "Title role (considered)",
       "edge": "That July, Anne Hathaway was considered for the title role;"
   },
   {
       "node_1": "Olivia Milch

In [17]:
!pwd
Prabir/knowledge_graph/data_input/cureus/movie.txt

/Prabir/knowledge_graph


In [33]:
save_file_path = "/Prabir/knowledge_graph/data_input/cureus/movie.txt"
wiki_link = "https://en.wikipedia.org/wiki/Spider-Man"

scrap_data(wiki_link, save_file_path)
print("scraping done") if scrap_data else print()

scraping done


## Setup

In [34]:
# !pip install langchain
# !pip install -U langchain-community
# !pip install unstructured
# !sudo apt-get install libmagic1
# !pip install yachalk
#ollama serve
#ollama run zephyr

In [35]:
import pandas as pd
import numpy as np
import os
from langchain.document_loaders import PyPDFLoader, UnstructuredPDFLoader, PyPDFium2Loader
from langchain.document_loaders import PyPDFDirectoryLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from pathlib import Path
import random

## Input data directory
data_dir = "cureus"
inputdirectory = Path(f"./data_input/{data_dir}")
## This is where the output csv files will be written
out_dir = data_dir
outputdirectory = Path(f"./data_output/{out_dir}")

## Load Documents

In [36]:
## Dir PDF Loader
# loader = PyPDFDirectoryLoader(inputdirectory)
## File Loader
# loader = PyPDFLoader("./data/MedicalDocuments/orf-path_health-n1.pdf")
loader = DirectoryLoader(inputdirectory, show_progress=True)
documents = loader.load()

splitter = RecursiveCharacterTextSplitter(
    chunk_size=1500,
    chunk_overlap=150,
    length_function=len,
    is_separator_regex=False,
)

pages = splitter.split_documents(documents)
# print("Number of chunks = ", len(pages))
# print(pages[3].page_content)


100%|██████████| 1/1 [00:00<00:00,  4.57it/s]


## Create a dataframe of all the chunks

In [37]:
from helpers.df_helpers import documents2Dataframe
df = documents2Dataframe(pages)
print(df.shape)
df.head()

(51, 3)


text  \
0  Spider-Man is a superhero in American comic bo...   
1  Spider-Man's secret identity is Peter Benjamin...   
2  When Spider-Man first appeared in the early 19...   
3  Marvel has featured Spider-Man in several comi...   
4  Spider-Man is one of the most popular and comm...   

                        source                          chunk_id  
0  data_input/cureus/movie.txt  72a057843e4547129ad9ea7f4d523b8b  
1  data_input/cureus/movie.txt  0af60be2eb4f44bab299bcf8905cc900  
2  data_input/cureus/movie.txt  c372aa2ec7f54ee6956e6ea427a4e6de  
3  data_input/cureus/movie.txt  f3ad949962f54d229f29a6cd384c267f  
4  data_input/cureus/movie.txt  85f81cc45219411fb6384daf09457c2a

## Extract Concepts

In [38]:
## This function uses the helpers/prompt function to extract concepts from text
from helpers.df_helpers import df2Graph
from helpers.df_helpers import graph2Df

If regenerate is set to True then the dataframes are regenerated and Both the dataframes are written in the csv format so we dont have to calculate them again. 

        dfne = dataframe of edges

        df = dataframe of chunks


Else the dataframes are read from the output directory

In [39]:
## To regenerate the graph with LLM, set this to True
regenerate = True

if regenerate:
    concepts_list = df2Graph(df, model='zephyr:latest')
    dfg1 = graph2Df(concepts_list)
    if not os.path.exists(outputdirectory):
        os.makedirs(outputdirectory)
    
    dfg1.to_csv(outputdirectory/"graph.csv", sep="|", index=False)
    df.to_csv(outputdirectory/"chunks.csv", sep="|", index=False)
else:
    dfg1 = pd.read_csv(outputdirectory/"graph.csv", sep="|")

dfg1.replace("", np.nan, inplace=True)
dfg1.dropna(subset=["node_1", "node_2", 'edge'], inplace=True)
dfg1['count'] = 4 
## Increasing the weight of the relation to 4. 
## We will assign the weight of 1 when later the contextual proximity will be calculated.  
print(dfg1.shape)
dfg1.head()

[
   {
       "node_1": "Spider-Man",
       "node_2": "Marvel Comics",
       "edge": "Spider-Man is a superhero published by Marvel Comics."
   },
   {
       "node_1": "Stan Lee",
       "node_2": "Spider-Man",
       "edge": "Spider-Man was created by writer-editor Stan Lee and artist Steve Ditko in the comic book Amazing Fantasy #15."
   },
   {
       "node_1": "Steve Ditko",
       "node_2": "Spider-Man",
       "edge": "Spider-Man was created by writer-editor Stan Lee and artist Steve Ditko in the comic book Amazing Fantasy #15."
   },
   {
       "node_1": "Silver Age of Comic Books",
       "node_2": "Spider-Man",
       "edge": "Spider-Man first appeared in the Silver Age of Comic Books, specifically in the anthology comic book Amazing Fantasy #15 (August 1962)."
   },
   {
       "node_1": "American comic books",
       "node_2": "Spider-Man",
       "edge": "Spider-Man is a superhero in American comic books published by Marvel Comics."
   }
][
   {
      "node_1": "Peter B

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [41]:
dfg1.head(20)

node_1                 node_2  \
0                  spider-man          marvel comics   
1                    stan lee             spider-man   
2                 steve ditko             spider-man   
3   silver age of comic books             spider-man   
4        american comic books             spider-man   
5       peter benjamin parker             spider-man   
6     richard and mary parker  peter benjamin parker   
7                    aunt may  peter benjamin parker   
8                   uncle ben  peter benjamin parker   
9              flash thompson  peter benjamin parker   
10           j. jonah jameson  peter benjamin parker   
11               harry osborn  peter benjamin parker   
12                 gwen stacy  peter benjamin parker   
13           mary jane watson  peter benjamin parker   
14                  black cat  peter benjamin parker   
15             doctor octopus  peter benjamin parker   
16               green goblin  peter benjamin parker   
17                      venom  peter benjamin parker   
18         radioactive spider  peter benjamin parker   
19               spider-sense  peter benjamin parker   

                                                 edge  \
0   Spider-Man is a superhero published by Marvel ...   
1   Spider-Man was created by writer-editor Stan L...   
2   Spider-Man was created by writer-editor Stan L...   
3   Spider-Man first appeared in the Silver Age of...   
4   Spider-Man is a superhero in American comic bo...   
5   Peter Parker initially used his spider powers ...   
6   Peter Parker's parents died in a plane crash a...   
7   Peter Parker was raised by his Aunt May and Un...   
8   Peter Parker was raised by his Aunt May and Un...   
9   Spider-Man (Peter Parker) had Flash Thompson a...   
10  Spider-Man (Peter Parker) had J. Jonah Jameson...   
11  Spider-Man (Peter Parker) had Harry Osborn as ...   
12  Spider-Man (Peter Parker) had Gwen Stacy as a ...   
13  Spider-Man (Peter Parker) had Mary Jane Watson...   
14  Spider-Man (Peter Parker) had the Black Cat as...   
15  Spider-Man (Peter Parker) had Doctor Octopus a...   
16  Spider-Man (Peter Parker) had Harry Osborn as ...   
17  Spider-Man (Peter Parker) had Venom as a symbi...   
18  Peter Parker gained his spider powers after be...   
19  Spider-Man (Peter Parker) has the ability to d...   

                            chunk_id  count  
0   72a057843e4547129ad9ea7f4d523b8b      4  
1   72a057843e4547129ad9ea7f4d523b8b      4  
2   72a057843e4547129ad9ea7f4d523b8b      4  
3   72a057843e4547129ad9ea7f4d523b8b      4  
4   72a057843e4547129ad9ea7f4d523b8b      4  
5   0af60be2eb4f44bab299bcf8905cc900      4  
6   0af60be2eb4f44bab299bcf8905cc900      4  
7   0af60be2eb4f44bab299bcf8905cc900      4  
8   0af60be2eb4f44bab299bcf8905cc900      4  
9   0af60be2eb4f44bab299bcf8905cc900      4  
10  0af60be2eb4f44bab299bcf8905cc900      4  
11  0af60be2eb4f44bab299bcf8905cc900      4  
12  0af60be2eb4f44bab299bcf8905cc900      4  
13  0af60be2eb4f44bab299bcf8905cc900      4  
14  0af60be2eb4f44bab299bcf8905cc900      4  
15  0af60be2eb4f44bab299bcf8905cc900      4  
16  0af60be2eb4f44bab299bcf8905cc900      4  
17  0af60be2eb4f44bab299bcf8905cc900      4  
18  0af60be2eb4f44bab299bcf8905cc900      4  
19  0af60be2eb4f44bab299bcf8905cc900      4

## Calculating contextual proximity

In [6]:
def contextual_proximity(df: pd.DataFrame) -> pd.DataFrame:
    ## Melt the dataframe into a list of nodes
    dfg_long = pd.melt(
        df, id_vars=["chunk_id"], value_vars=["node_1", "node_2"], value_name="node"
    )
    dfg_long.drop(columns=["variable"], inplace=True)
    # Self join with chunk id as the key will create a link between terms occuring in the same text chunk.
    dfg_wide = pd.merge(dfg_long, dfg_long, on="chunk_id", suffixes=("_1", "_2"))
    # drop self loops
    self_loops_drop = dfg_wide[dfg_wide["node_1"] == dfg_wide["node_2"]].index
    dfg2 = dfg_wide.drop(index=self_loops_drop).reset_index(drop=True)
    ## Group and count edges.
    dfg2 = (
        dfg2.groupby(["node_1", "node_2"])
        .agg({"chunk_id": [",".join, "count"]})
        .reset_index()
    )
    dfg2.columns = ["node_1", "node_2", "chunk_id", "count"]
    dfg2.replace("", np.nan, inplace=True)
    dfg2.dropna(subset=["node_1", "node_2"], inplace=True)
    # Drop edges with 1 count
    dfg2 = dfg2[dfg2["count"] != 1]
    dfg2["edge"] = "contextual proximity"
    return dfg2


dfg2 = contextual_proximity(dfg1)
dfg2.tail()

node_1          node_2  \
2827  world-class health facilities  nhm strategies   
2828  world-class health facilities     rural areas   
2829  world-class health facilities    social norms   
2830  world-class health facilities     urban areas   
2831  world-class health facilities     urban slums   

                                               chunk_id  count  \
2827  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...     10   
2828  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...      2   
2829  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...      2   
2830  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...      2   
2831  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...      2   

                      edge  
2827  contextual proximity  
2828  contextual proximity  
2829  contextual proximity  
2830  contextual proximity  
2831  contextual proximity

### Merge both the dataframes

In [7]:
dfg = pd.concat([dfg1, dfg2], axis=0)
dfg = (
    dfg.groupby(["node_1", "node_2"])
    .agg({"chunk_id": ",".join, "edge": ','.join, 'count': 'sum'})
    .reset_index()
)
dfg

node_1  \
0                      56 articles   
1                             [54]   
2                             [55]   
3                  a bad situation   
4            a worrisome new trend   
..                             ...   
753  world-class health facilities   
754  world-class health facilities   
755  world-class health facilities   
756  world-class health facilities   
757  world-class health facilities   

                                               node_2  \
0                         extensive literature search   
1    increasing violence against healthcare personnel   
2    increasing violence against healthcare personnel   
3    increasing violence against healthcare personnel   
4    increasing violence against healthcare personnel   
..                                                ...   
753                                    nhm strategies   
754                                       rural areas   
755                                      social norms   
756                                       urban areas   
757                                       urban slums   

                                              chunk_id                  edge  \
0    d7a3e5085c7f4de4bc28fb0bd9cb0a94,d7a3e5085c7f4...  contextual proximity   
1    640835e2521045a395ab6465cc1ba4ca,640835e252104...  contextual proximity   
2    640835e2521045a395ab6465cc1ba4ca,640835e252104...  contextual proximity   
3    640835e2521045a395ab6465cc1ba4ca,640835e252104...  contextual proximity   
4    640835e2521045a395ab6465cc1ba4ca,640835e252104...  contextual proximity   
..                                                 ...                   ...   
753  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...  contextual proximity   
754  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...  contextual proximity   
755  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...  contextual proximity   
756  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...  contextual proximity   
757  0857ab4513ad4383aed095bcf24506fa,0857ab4513ad4...  contextual proximity   

     count  
0        2  
1        2  
2        2  
3        2  
4        2  
..     ...  
753     10  
754      2  
755      2  
756      2  
757      2  

[758 rows x 5 columns]

## Calculate the NetworkX Graph

In [8]:
nodes = pd.concat([dfg['node_1'], dfg['node_2']], axis=0).unique()
nodes.shape

(215,)

In [9]:
import networkx as nx
G = nx.Graph()

## Add nodes to the graph
for node in nodes:
    G.add_node(
        str(node)
    )

## Add edges to the graph
for index, row in dfg.iterrows():
    G.add_edge(
        str(row["node_1"]),
        str(row["node_2"]),
        title=row["edge"],
        weight=row['count']/4
    )

### Calculate communities for coloring the nodes

In [10]:
communities_generator = nx.community.girvan_newman(G)
top_level_communities = next(communities_generator)
next_level_communities = next(communities_generator)
communities = sorted(map(sorted, next_level_communities))
print("Number of Communities = ", len(communities))
print(communities)

Number of Communities =  17
[['56 articles', 'analysis', "corresponding authors' experiential knowledge", 'extensive literature search', 'peer-reviewed journals'], ['[54]', '[55]', 'a bad situation', 'a worrisome new trend', 'adequately compensated', 'can reverse the situation', 'defensive medicine practices', 'increasing violence against healthcare personnel', 'intense focus on specialization', 'low physician-to-patient ratio', 'overwhelmed physicians', 'primary care physicians', 'private marketplace', 'protect themselves by ordering unnecessary tests and procedures', 'results in delays in attending patients', 'set in', 'tempted to take on more patients than they can reasonably serve', 'thoughtful approach to government planning', 'underpaid physicians', 'unethical practices by pharmaceutical companies', 'will not be able to solve this'], ['accredit health facilities', 'enforcement of existing rules', 'health insurance scheme for central government employees', 'health system standardi

### Create a dataframe for community colors

In [11]:
import seaborn as sns
palette = "hls"

## Now add these colors to communities and make another dataframe
def colors2Community(communities) -> pd.DataFrame:
    ## Define a color palette
    p = sns.color_palette(palette, len(communities)).as_hex()
    random.shuffle(p)
    rows = []
    group = 0
    for community in communities:
        color = p.pop()
        group += 1
        for node in community:
            rows += [{"node": node, "color": color, "group": group}]
    df_colors = pd.DataFrame(rows)
    return df_colors


colors = colors2Community(communities)
colors

node    color  group
0                                      56 articles  #db57db      1
1                                         analysis  #db57db      1
2    corresponding authors' experiential knowledge  #db57db      1
3                      extensive literature search  #db57db      1
4                           peer-reviewed journals  #db57db      1
..                                             ...      ...    ...
210                rural medical assistants (rmas)  #57bcdb     15
211                                 limited uptake  #db57ac     16
212             national health protection mission  #db57ac     16
213                  private health sector systems  #57dbcc     17
214                                         public  #57dbcc     17

[215 rows x 3 columns]

### Add colors to the graph

In [12]:
for index, row in colors.iterrows():
    G.nodes[row['node']]['group'] = row['group']
    G.nodes[row['node']]['color'] = row['color']
    G.nodes[row['node']]['size'] = G.degree[row['node']]

In [13]:
from pyvis.network import Network

graph_output_directory = "./docs/index.html"

net = Network(
    notebook=False,
    # bgcolor="#1a1a1a",
    cdn_resources="remote",
    height="900px",
    width="100%",
    select_menu=True,
    # font_color="#cccccc",
    filter_menu=False,
)

net.from_nx(G)
# net.repulsion(node_distance=150, spring_length=400)
net.force_atlas_2based(central_gravity=0.015, gravity=-31)
# net.barnes_hut(gravity=-18100, central_gravity=5.05, spring_length=380)
net.show_buttons(filter_=["physics"])

net.show(graph_output_directory, notebook=False)

./docs/index.html
